In [1]:
import time

class Stack:
     def __init__(self):
         self.items = []
         '''last leaf is a left child'''
         self.tag = 0 

     def isEmpty(self):
         return self.items == []

     def push(self, item):
         self.items.append(item)

     def pop(self):
         return self.items.pop()

     def peek(self):
         return self.items[len(self.items)-1]

     def size(self):
         return len(self.items)
    
    
class TreeNode:
    def __init__(self,key,val,left=None,right=None,parent=None):
        '''key is a integer in this scenario'''
        self.key = key 
        '''payload is used for storing rank value in this scenario'''
        self.payload = val 
        self.leftChild = left
        self.rightChild = right
        self.parent = parent
        self.nodeTraceQ=Stack()

    def getKey(self):
        return self.key
    
    def getValue(self):
        return self.payload
        
    def hasLeftChild(self):
        return self.leftChild

    def hasRightChild(self):
        return self.rightChild

    def isLeftChild(self):
        return self.parent and self.parent.leftChild == self

    def isRightChild(self):
        return self.parent and self.parent.rightChild == self

    def isRoot(self):
        return not self.parent

    def isLeaf(self):
        return not (self.rightChild or self.leftChild)

    def hasAnyChildren(self):
        return self.rightChild or self.leftChild

    def hasBothChildren(self):
        return self.rightChild and self.leftChild
        
    def findSuccessor(self,nodeTraceQ):
        succ = None
        
        if self.hasRightChild():
            succ = self.rightChild.findMin(nodeTraceQ)
        else:
            if self.parent:
                if self.isLeftChild():
                    
                    nodeTraceQ.push(self.parent)
                    succ = self.parent
                else:
                    
                    nodeTraceQ.push(self.parent)
                    self.parent.rightChild = None
                    succ = self.parent.findSuccessor(nodeTraceQ)
                    self.parent.rightChild = self
                    
        
        return succ

    def findMin(self,nodeTraceQ):
        current = self
        while current.hasLeftChild():
            
            nodeTraceQ.push(current)
            current = current.leftChild
            
        nodeTraceQ.push(current)
        return current
            
            
class BinarySearchTree:

    def __init__(self,alist=None):       
        self.root = None
        self.size = 0
        self.enablePrint = True
        self.iterEndTime = 0
        '''use a queue to record the node that encountered in a traversal route'''
        self.traceQ = Stack()
        '''traceQ will be all popped out into stepQ for step print'''
        self.stepQ = Stack()        
        '''a switch to control the print of the route detail'''
        self.traceTraversalRoute = False
        if alist:
            for item in alist:
                '''initialize all the node rank to be 0'''
                self.put(item,0)
            self.initNodeRank()
            self.count = self.size

            
    def length(self):
        return self.size

    def __len__(self):
        return self.size
    
    def enableTrace(self,enable=True):
        '''
           enable or disable the trace queue,
           it will reset the queue once called
        '''
        self.traceTraversalRoute=enable
        if not self.traceQ.isEmpty():
            while self.traceQ.size()>0:
                self.traceQ.pop()
        if not self.stepQ.isEmpty():
            while self.stepQ.size()>0:
                self.stepQ.pop()
 
    def disablePrint(self):
        '''
           diable all the print in the tree 
           for large amount test
        '''
        self.enablePrint = False
    
    def insertNode(self, treeNode):
        self.put(treeNode.getKey(),treeNode.getValue())
        self.count = self.size
    
    def insertList(self, alist):
        if not alist:
            print "no action for vacant list"
        else:
            for item in alist:
                 self.put(item,0)
                 self.size = self.size+1
                    
    def initNodeRank(self):
        '''
           Initialize the rank value of all the tree nodes, 
           root node is 0, left child equals to parent rank value minus 1,
           right child equals to parent rank value plus 1
        '''
        if not self:
            return
        self.root.payload = 0
        self.preorderInit(self.root)

    
    def preorderInit(self,currentNode):
        '''helper function for initNodeRank'''
        if not currentNode:
            return   
        else:      
        
            if currentNode.isLeftChild():   
                currentNode.payload = currentNode.parent.payload-1
            if currentNode.isRightChild():
                currentNode.payload = currentNode.parent.payload+1
            if currentNode.hasLeftChild():
                self.preorderInit(currentNode.leftChild)
            if currentNode.hasRightChild():
                self.preorderInit(currentNode.rightChild)
            
    
            
    def printTree(self):
        '''traverse the tree in inorder and print only distinguished nodes'''
        if self.root:
            self.inorderPrint(self.root)
        else:     
            print "this is a vacant tree." 

    def printIterSteps(self):
        '''print all the nodes iterated including distinguished nodes during traversal'''
        if self.traceQ.isEmpty():
            print "nothing found in trace queue."
            return
        else:
            
            while self.traceQ.size() >0:
                self.stepQ.push(self.traceQ.pop())
             
            maxNode=self.findRightMost(self.root).getKey()
            num = 0
            while self.stepQ.size()>0:
                num = num + 1
                node = self.stepQ.pop()
                if  self.enablePrint:
                    print "--------------------------------"
                    print "Step:%4d | Node:%4d | Rank:%4d"%(num,node.getKey(),node.getValue())
                    print "--------------------------------"
                
                if node.getKey()== maxNode:  
                    if self.traceQ.tag == 0:
                        '''max node has no left child'''
                        break
                    else:
                        '''
                        max node has left child, now set to 0,
                        and traverse one more time
                        '''
                        self.traceQ.tag = 0
                        continue
               
                
                
                
        if self.enablePrint:
            print "Total: %4d nodes traversed"%num
        return num
            
            
    def inorderIterNode(self,key):
        '''traverse any node in inorder'''
        currentNode = self._get(key,self.root)
        if currentNode.isRoot():
           self.printTree()
        else:
           self.inorderPrint(currentNode)
    
        
    def inorderPrint(self,currentNode):
        '''helper function for inorder traversal'''
        
        if currentNode.hasLeftChild():
            self.traceQ.push(currentNode) if self.traceTraversalRoute else ''
            self.inorderPrint(currentNode.leftChild)
        self.traceQ.push(currentNode) if self.traceTraversalRoute else ''
        if self.enablePrint:
            print "-----------------------------------"
            print ("Distinguished Node:%4d , Rank:%4d" % (currentNode.getKey(),currentNode.getValue()))
            print "-----------------------------------"
        self.count = self.count - 1
        if currentNode.hasRightChild() :
            self.inorderPrint(currentNode.rightChild)
            self.traceQ.push(currentNode) if self.traceTraversalRoute else ''
        if self.count == 0:
            self.count = self.count - 1
            self.iterEndTime = time.time()
            if currentNode.hasLeftChild():
                self.traceQ.tag = 1
           
                
    def getIterEndTime(self):
        return self.iterEndTime
    
    def resetIterEndTime(self):
        self.iterEndTime = 0
    
    def inorderNext(self,key):
        '''find the successor according to any specified node key'''
        self.traceQ.tag = 1
        '''step1, locate the node and put the traced nodes into traceQ'''
        currentNode = self._get(key,self.root)
        self.traceQ.push(currentNode)
        '''step2, give the found node a stack, 
           and ask it to find its successor
           meanwhile record all the node it the stack
        '''
        tempQ = Stack()
        res = currentNode.findSuccessor(tempQ)
        
        '''merge the two stack into step print Stack'''
        while tempQ.size() > 0:
            self.stepQ.push(tempQ.pop())
        while tempQ.size() > 0:
            self.stepQ.push(self.traceQ.pop())
        return res 
        
        
   
    def inorderFirst(self):
        '''find the first node in inorder traversal'''
        if self.root and self.root.hasLeftChild():
            node=self.findLeftMost(self.root)
            return node
        else:
            return None
    
    def findLeftMost(self,currentNode):
        '''
          This is a duplicate function defined in TreeNode,
          should have deprecated this one.
        '''
        '''helper function for inorderNext'''
        if not currentNode:
            return
        while currentNode.hasLeftChild():

            self.traceQ.push(currentNode) if self.traceTraversalRoute else ''
            currentNode = currentNode.leftChild
    
        self.traceQ.push(currentNode) if self.traceTraversalRoute else ''
        return currentNode
    
    def findRightMost(self,currentNode):
        if not currentNode:
            return
        while currentNode.hasRightChild():
            currentNode = currentNode.rightChild
            
        return currentNode
    
    def put(self,key,val):
        if self.root:
            self._put(key,val,self.root)
        else:
            self.root = TreeNode(key,val)
        self.size = self.size + 1

    def _put(self,key,val,currentNode):
        if key < currentNode.key:
            if currentNode.hasLeftChild():
                   self._put(key,val,currentNode.leftChild)
            else:
                   currentNode.leftChild = TreeNode(key,val,parent=currentNode)
        else:
            if currentNode.hasRightChild():
                   self._put(key,val,currentNode.rightChild)
            else:
                   currentNode.rightChild = TreeNode(key,val,parent=currentNode)

    def _get(self,key,currentNode):
        if not currentNode:
            return None
        elif currentNode.key == key:
            return currentNode
        elif key < currentNode.key:
            self.traceQ.push(currentNode) if self.traceTraversalRoute else ''
            return self._get(key,currentNode.leftChild)
        else:
            self.traceQ.push(currentNode) if self.traceTraversalRoute else ''
            return self._get(key,currentNode.rightChild)

In [28]:
import random, time
import numpy as np

nodeNumdict = {}
iterStepdict = {}
timeComplexdict = {}

for i in range(1,11):
    
    for treeSize in range(50,150,1):
        '''
        build 50 trees with node number from 50 to 100,
        all the integer insert is randomly selected
        '''
        mylist = [random.randint(0,treeSize) for r in xrange(treeSize)]
        mytree = BinarySearchTree(mylist)
        mytree.enableTrace()
        mytree.disablePrint()
        start = time.time()
        mytree.printTree()
        end = mytree.getIterEndTime()
        steps = mytree.printIterSteps()
        nodeNumdict[i] = treeSize
        iterStepdict[i] = steps
        timeComplexdict[i]=end-start

sumNodeNumList = nodeNumdict[1]
sumIterStepList = iterStepdict[1]
sumTimeComplex = timeComplexdict[1]
        
for i in nodeNumdict:
    if i==1:
        continue
    sumNodeNumList = np.add(sumNodeNumList,nodeNumdict[i]).tolist()
    
for i in iterStepdict:
    if i==1:
        continue
    sumIterStepList = np.add(sumIterStepList,iterStepdict[i]).tolist()

for i in timeComplexdict:
    if i==1:
        continue
    sumTimeComplex = np.add(sumTimeComplex,timeComplexdict[i]).tolist()
    


IndentationError: expected an indented block (<ipython-input-28-f046fb9df5ba>, line 14)

In [17]:
import random
import time

nodeNumList = []
iterStepList = []
timeComplex = []


for treeSize in range(50,150,1):
    '''
    build 50 trees with node number from 50 to 100,
    all the integer insert is randomly selected
    '''
    mylist = [random.randint(0,treeSize) for r in xrange(treeSize)]
    mytree = BinarySearchTree(mylist)
    mytree.enableTrace()
    mytree.disablePrint()
    start = time.time()
    mytree.printTree()
    end = mytree.getIterEndTime()
    steps = mytree.printIterSteps()
    nodeNumList.append(treeSize)
    iterStepList.append(steps)
    timeComplex.append(end-start)
    #print mylist

#print nodeNumList
#print iterStepList
#print timeComplex

-----------------------------------
Distinguished Node:   1 , Rank:  -2
-----------------------------------
-----------------------------------
Distinguished Node:   4 , Rank:  -1
-----------------------------------
-----------------------------------
Distinguished Node:   5 , Rank:  -2
-----------------------------------
-----------------------------------
Distinguished Node:   5 , Rank:  -1
-----------------------------------
-----------------------------------
Distinguished Node:   6 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   6 , Rank:   1
-----------------------------------
-----------------------------------
Distinguished Node:   6 , Rank:   2
-----------------------------------
-----------------------------------
Distinguished Node:   8 , Rank:  -1
-----------------------------------
-----------------------------------
Distinguished Node:   9 , Rank:   0
-----------------------------------
----------------------------

In [12]:
import graphlab
from graphlab import SFrame

A newer version of GraphLab Create (v1.8.2) is available! Your current version is v1.7.1.

You can use pip to upgrade the graphlab-create package. For more information see https://dato.com/products/create/upgrade.


In [13]:
treeSF = SFrame({'Node Count':nodeNumList,'Iteration Steps':iterStepList, 'Time Complexity':timeComplex})
treeSF.print_rows(num_rows=50)

[INFO] 1456195433 : INFO:     (initialize_globals_from_environment:282): Setting configuration variable GRAPHLAB_FILEIO_ALTERNATIVE_SSL_CERT_FILE to /Users/ziqxu/anaconda/envs/dato-env/lib/python2.7/site-packages/certifi/cacert.pem
1456195433 : INFO:     (initialize_globals_from_environment:282): Setting configuration variable GRAPHLAB_FILEIO_ALTERNATIVE_SSL_CERT_DIR to 
This non-commercial license of GraphLab Create is assigned to jared.ziqxu@gmail.com and will expire on February 03, 2017. For commercial licensing options, visit https://dato.com/buy/.

[INFO] Start server at: ipc:///tmp/graphlab_server-68559 - Server binary: /Users/ziqxu/anaconda/envs/dato-env/lib/python2.7/site-packages/graphlab/unity_server - Server log: /tmp/graphlab_server_1456195433.log
[INFO] GraphLab Server Version: 1.7.1


+-----------------+------------+-------------------+
| Iteration Steps | Node Count |  Time Complexity  |
+-----------------+------------+-------------------+
|        98       |     50     | 0.000128030776978 |
|        94       |     51     | 0.000133037567139 |
|       102       |     52     | 0.000137090682983 |
|        78       |     53     | 0.000159025192261 |
|       104       |     54     | 0.000150918960571 |
|       104       |     55     |  0.00014591217041 |
|       109       |     56     | 0.000216960906982 |
|       104       |     57     | 0.000150918960571 |
|       113       |     58     | 0.000150918960571 |
|        97       |     59     | 0.000142812728882 |
|        89       |     60     | 0.000149011611938 |
|       113       |     61     | 0.000156164169312 |
|       114       |     62     | 0.000444889068604 |
|       119       |     63     | 0.000164031982422 |
|       125       |     64     | 0.000282049179077 |
|       128       |     65     |  0.0001831054

In [14]:
graphlab.canvas.set_target('ipynb')

In [15]:
treeSF.show(view="Scatter Plot",x="Node Count", y="Iteration Steps")

In [16]:
treeSF.show(view="Scatter Plot",x="Node Count", y="Time Complexity")

In [7]:
mylist = range(0,11)
mytree = BinarySearchTree()
print mylist[1:]

def buildTree(alist,atree):
    
    if len(alist)>1:
        mid = len(alist)//2
        mynode=TreeNode(alist[mid],0)
        atree.insertNode(mynode)
        lefthalf = alist[:mid]
        righthalf = alist[mid:]
        buildTree(lefthalf,atree)
        buildTree(righthalf,atree)
        

buildTree(mylist,mytree)
mytree.initNodeRank()
mytree.enableTrace()
mytree.disablePrint()


steps = 0
for i in mylist[1:-1]:
    mytree.enableTrace()
    mytree.inorderNext(i)
    istep = mytree.printIterSteps()
    steps = steps + istep
print "Total Steps: %d"%steps


[1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
Total Steps: 38


In [132]:
alist = range(1,11)
print alist
mytree = BinarySearchTree(alist)
mytree.enableTrace()
#mytree.disablePrint()
steps = 0

for i in alist[0:-1]:
    
    mytree.inorderNext(i)
    istep = mytree.printIterSteps()
    steps = steps + istep

print steps


[1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
inorderNext 1
traceQ111 size is 0
traceQ999 size is 0
currentNode111 1 , enqueue 1
traceQ size is 2
stepQ size is 0
again traceQ size is 0
again stepQ size is 2
maxNode is 10
--------------------------------
Step:   1 | Node:   1 | Rank:   0
--------------------------------
--------------------------------
Step:   2 | Node:   2 | Rank:   1
--------------------------------
Total:    2 nodes traversed
inorderNext 2
traceQ111 size is 0
traceQ999 size is 1
currentNode111 2 , enqueue 2
traceQ size is 3
stepQ size is 0
again traceQ size is 0
again stepQ size is 3
maxNode is 10
--------------------------------
Step:   1 | Node:   1 | Rank:   0
--------------------------------
--------------------------------
Step:   2 | Node:   2 | Rank:   1
--------------------------------
--------------------------------
Step:   3 | Node:   3 | Rank:   2
--------------------------------
Total:    3 nodes traversed
inorderNext 3
traceQ111 size is 0
traceQ999 size is 2
currentN

In [137]:
mytree = BinarySearchTree([15,10,9,12,11,18,16,20,17])
#print mytree.count
mytree.enableTrace()
print mytree.inorderNext(17).getKey()
#mytree.printTree()
#print mytree.traceQ.size()
mytree.printIterSteps()

findsuccessor 333 17 is right child, enqueue 16
findsuccessor 222 16 is left child, enqueue 18
18
traceQ size is 4
stepQ size is 2
again traceQ size is 0
again stepQ size is 6
maxNode is 20
--------------------------------
Step:   1 | Node:  15 | Rank:   0
--------------------------------
--------------------------------
Step:   2 | Node:  18 | Rank:   1
--------------------------------
--------------------------------
Step:   3 | Node:  16 | Rank:   0
--------------------------------
--------------------------------
Step:   4 | Node:  17 | Rank:   1
--------------------------------
--------------------------------
Step:   5 | Node:  16 | Rank:   0
--------------------------------
--------------------------------
Step:   6 | Node:  18 | Rank:   1
--------------------------------
Total:    6 nodes traversed


6

In [93]:
alist = range(0,11)
mytree = BinarySearchTree()
print alist[1:]

def buildTree(alist):
    
    if len(alist)>1:
        mid = len(alist)//2
        mynode=TreeNode(alist[mid],0)
        mytree.insertNode(mynode)
        lefthalf = alist[:mid]
        righthalf = alist[mid:]
        buildTree(lefthalf)
        buildTree(righthalf)
        

buildTree(alist)
#mytree.initNodeRank()
mytree.enableTrace()
#mytree.printIterSteps()
#mytree.disablePrint()
mytree.printTree()
mytree.printIterSteps()

'''
steps = 0
for i in alist[1:-1]:
    mytree.enableTrace()
    print "i = %d"%i
    mytree.inorderNext(i)
    istep = mytree.printIterSteps()
    print "istep:%d"%istep
    #steps = steps + istep
print "Total Steps: %d"%steps
'''

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
-----------------------------------
Distinguished Node:   1 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   2 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   3 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   4 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   5 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   6 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   7 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   8 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   9 , Rank:   0
--------------------------------

'\nsteps = 0\nfor i in alist[1:-1]:\n    mytree.enableTrace()\n    print "i = %d"%i\n    mytree.inorderNext(i)\n    istep = mytree.printIterSteps()\n    print "istep:%d"%istep\n    #steps = steps + istep\nprint "Total Steps: %d"%steps\n'

In [65]:
alist = range(1,11)
print alist
mytree = BinarySearchTree(alist)
mytree.initNodeRank()
mytree.enableTrace()
mytree.disablePrint()
mytree.printIterSteps()
#steps = 0
#for i in alist[1:]:
#    mytree.inorderNext(i)
#    istep = mytree.printIterSteps()
#    steps = steps + istep
#print steps

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
nothing found in trace queue.


In [51]:
alist = range(19,11,-1)
mylist = [11]+alist
mytree = BinarySearchTree(mylist)
mytree.enableTrace()
print(mytree.inorderNext(11).getKey())
mytree.printIterSteps()
#mytree.inorderFirst().getKey()

12
Total:    9 nodes traversed


9

In [44]:
import random
import time

nodeNumList = []
iterStepList = []
timeComplex = []

for treeSize in range(50,150,1):
    '''
    build 50 trees with node number from 50 to 100,
    all the integer insert is randomly selected
    '''
    mylist = [random.randint(0,treeSize) for r in xrange(treeSize)]
    mytree = BinarySearchTree(mylist)
    mytree.enableTrace()
    start = time.time()
    mytree.printTree()
    end = time.time()
    steps = mytree.printIterSteps()
    nodeNumList.append(treeSize)
    iterStepList.append(steps)
    timeComplex.append(end-start)
    #print mylist

print nodeNumList
print iterStepList
print timeComplex

-----------------------------------
Distinguished Node:   0 , Rank:  -1
-----------------------------------
-----------------------------------
Distinguished Node:   1 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   2 , Rank:  -4
-----------------------------------
-----------------------------------
Distinguished Node:   2 , Rank:  -3
-----------------------------------
-----------------------------------
Distinguished Node:   3 , Rank:  -3
-----------------------------------
-----------------------------------
Distinguished Node:   3 , Rank:  -2
-----------------------------------
-----------------------------------
Distinguished Node:   4 , Rank:  -2
-----------------------------------
-----------------------------------
Distinguished Node:   4 , Rank:  -2
-----------------------------------
-----------------------------------
Distinguished Node:   6 , Rank:  -1
-----------------------------------
----------------------------

In [42]:
import graphlab
from graphlab import SFrame
#sf = SFrame({'Node Count':nodeNumList,'Iteration Steps':iterStepList})

A newer version of GraphLab Create (v1.8.2) is available! Your current version is v1.8.1.

You can use pip to upgrade the graphlab-create package. For more information see https://dato.com/products/create/upgrade.


In [48]:
treeSF = SFrame({'Node Count':nodeNumList,'Iteration Steps':iterStepList, 'Time Complexity':timeComplex})
#treeSF.print_rows(num_rows=50)
treeSF.tail(50)

Columns:
	Iteration Steps	int
	Node Count	int
	Time Complexity	float

Rows: 50

Data:
+-----------------+------------+------------------+
| Iteration Steps | Node Count | Time Complexity  |
+-----------------+------------+------------------+
|       139       |    100     | 0.0204119682312  |
|       145       |    101     | 0.0100719928741  |
|       142       |    102     | 0.0144009590149  |
|       147       |    103     | 0.0261490345001  |
|       147       |    104     | 0.0144329071045  |
|       148       |    105     | 0.0146930217743  |
|       155       |    106     |  0.016312122345  |
|       151       |    107     | 0.0306370258331  |
|       156       |    108     | 0.0165259838104  |
|       152       |    109     | 0.00791811943054 |
+-----------------+------------+------------------+
[50 rows x 3 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [61]:
sf.head()

Columns:
	Iteration Steps	int
	Node Count	int

Rows: 10

Data:
+-----------------+------------+
| Iteration Steps | Node Count |
+-----------------+------------+
|        69       |     50     |
|        74       |     51     |
|        74       |     52     |
|        76       |     53     |
|        78       |     54     |
|        80       |     55     |
|        77       |     56     |
|        77       |     57     |
|        82       |     58     |
|        84       |     59     |
+-----------------+------------+
[10 rows x 2 columns]

In [80]:
treeSF.show(view="Line Chart", x="Node Count", y="Iteration Steps")

Canvas is accessible via web browser at the URL: http://localhost:57298/index.html
Opening Canvas in default web browser.


In [34]:
mytree.enableTrace()
mytree.inorderFirst().getKey()
mytree.printIterSteps()

--------------------------------
Step:   1 | Node:  15 | Rank:   0
--------------------------------
--------------------------------
Step:   2 | Node:  10 | Rank:  -1
--------------------------------
--------------------------------
Step:   3 | Node:   9 | Rank:  -2
--------------------------------
Total:    3 nodes traversed


In [20]:
print(mytree.inorderNext(11).getKey())

12


In [21]:
print(mytree.inorderNext(15).getKey())

16


In [6]:
#mylist = range(10,19)

mytree = BinarySearchTree([15,10,9,12,11,18,16,20,17])
mytree.enableTrace()
print(mytree.inorderNext(10).getKey())
mytree.printIterSteps()

11
--------------------------------
Step:   1 | Node:  15 | Rank:   0
--------------------------------
--------------------------------
Step:   2 | Node:  10 | Rank:  -1
--------------------------------
--------------------------------
Step:   3 | Node:  12 | Rank:   0
--------------------------------
--------------------------------
Step:   4 | Node:  11 | Rank:  -1
--------------------------------
Total:    4 nodes traversed


4

In [26]:
mylist = range(10,19)
print mylist
mytree = BinarySearchTree(mylist)
mytree.enableTrace()
mytree.printTree()
mytree.printIterSteps()

[10, 11, 12, 13, 14, 15, 16, 17, 18]
-----------------------------------
Distinguished Node:  10 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:  11 , Rank:   1
-----------------------------------
-----------------------------------
Distinguished Node:  12 , Rank:   2
-----------------------------------
-----------------------------------
Distinguished Node:  13 , Rank:   3
-----------------------------------
-----------------------------------
Distinguished Node:  14 , Rank:   4
-----------------------------------
-----------------------------------
Distinguished Node:  15 , Rank:   5
-----------------------------------
-----------------------------------
Distinguished Node:  16 , Rank:   6
-----------------------------------
-----------------------------------
Distinguished Node:  17 , Rank:   7
-----------------------------------
-----------------------------------
Distinguished Node:  18 , Rank:   8
---------------------------

In [5]:
mytree = BinarySearchTree([15,10,9,12,11,18,16,20,17])
mytree.enableTrace()
mytree.printTree()
mytree.printIterSteps()

-----------------------------------
Distinguished Node:   9 , Rank:  -2
-----------------------------------
-----------------------------------
Distinguished Node:  10 , Rank:  -1
-----------------------------------
-----------------------------------
Distinguished Node:  11 , Rank:  -1
-----------------------------------
-----------------------------------
Distinguished Node:  12 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:  15 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:  16 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:  17 , Rank:   1
-----------------------------------
-----------------------------------
Distinguished Node:  18 , Rank:   1
-----------------------------------
-----------------------------------
Distinguished Node:  20 , Rank:   2
-----------------------------------
----------------------------

17

In [19]:
mytree.enableTrace()
mytree.printTree()
mytree.printIterSteps()

-----------------------------------
Distinguished Node:   9 , Rank:  -2
-----------------------------------
-----------------------------------
Distinguished Node:  10 , Rank:  -1
-----------------------------------
-----------------------------------
Distinguished Node:  11 , Rank:  -1
-----------------------------------
-----------------------------------
Distinguished Node:  12 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:  15 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:  16 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:  17 , Rank:   1
-----------------------------------
-----------------------------------
Distinguished Node:  18 , Rank:   1
-----------------------------------
-----------------------------------
Distinguished Node:  20 , Rank:   2
-----------------------------------
----------------------------

In [14]:
#mytree = BinarySearchTree([4,10,9,8,7,6])
#mytree.initNodeRank()
mytree.enableTrace()
#print(mytree.inorderNext(4).getKey())
#mytree.printTree()
#mytree.enableTrace(False)
#mytree.printTree()
#print(mytree.traceQ.size())
mytree.printIterSteps()

-----------------------------------
Distinguished Node:   4 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:   6 , Rank:  -3
-----------------------------------
-----------------------------------
Distinguished Node:   7 , Rank:  -2
-----------------------------------
-----------------------------------
Distinguished Node:   8 , Rank:  -1
-----------------------------------
-----------------------------------
Distinguished Node:   9 , Rank:   0
-----------------------------------
-----------------------------------
Distinguished Node:  10 , Rank:   1
-----------------------------------
--------------------------------
Step:   1 | Node:   4 | Rank:   0
--------------------------------
--------------------------------
Step:   2 | Node:  10 | Rank:   1
--------------------------------
--------------------------------
Step:   3 | Node:   9 | Rank:   0
--------------------------------
--------------------------------
Step:   4 | Node:  

In [203]:
mytree = BinarySearchTree([7,2,3,5,8,9,10,6,4])
#mytree.buildTreeWithList([7,2,3,5,8,9,10,6,4])
#mytree.printTree()
mytree.initNodeRank()
mytree.printTree()
print(mytree.inorder_next(6).getKey())
mytree.size

Traverse the tree with inorder:
Key:2 , Rank:-1
Key:3 , Rank:0
Key:4 , Rank:0
Key:5 , Rank:1
Key:6 , Rank:0
Key:7 , Rank:0
Key:8 , Rank:1
Key:9 , Rank:2
Key:10 , Rank:3
7


9

In [206]:
import random
import timeit
import time

length = 100
#mylist = [random.randint(0,length) for r in xrange(length)]
mylist = range(6,length)
print mylist


start = time.time()
#mytree.buildTreeWithList(mylist)
mytree = BinarySearchTree(mylist)
end = time.time()
print ("spent %10.9f time to build the tree with %d nodes" % (end-start, length))
mytree.initNodeRank()
start = time.time()
mytree.printTree()
end = time.time()
print ("spent %10.9f time to travese the tree with %d nodes in inorder" % (end-start, mytree.length()))

print "\n reverse the list and build a different tree"
print mylist[::-1]
mytree2 = BinarySearchTree(mylist[::-1])
#mytree2.buildTreeWithList(mylist[::-1])
mytree2.initNodeRank()
start = time.time()
mytree2.printTree()
end = time.time()
print ("spent %10.9f time to travese the revertree with %d nodes in inorder" % (end-start, mytree2.length()))


[6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99]
spent 0.006330013 time to build the tree with 100 nodes
Traverse the tree with inorder:
Key:6 , Rank:0
Key:7 , Rank:1
Key:8 , Rank:2
Key:9 , Rank:3
Key:10 , Rank:4
Key:11 , Rank:5
Key:12 , Rank:6
Key:13 , Rank:7
Key:14 , Rank:8
Key:15 , Rank:9
Key:16 , Rank:10
Key:17 , Rank:11
Key:18 , Rank:12
Key:19 , Rank:13
Key:20 , Rank:14
Key:21 , Rank:15
Key:22 , Rank:16
Key:23 , Rank:17
Key:24 , Rank:18
Key:25 , Rank:19
Key:26 , Rank:20
Key:27 , Rank:21
Key:28 , Rank:22
Key:29 , Rank:23
Key:30 , Rank:24
Key:31 , Rank:25
Key:32 , Rank:26
Key:33 , Rank:27
Key:34 , Rank:28
Key:35 , Rank:29
Key:36 , Rank:30
Key:37 , Rank:31
Key:38 , 